In [1]:
import matplotlib as mpl
import matplotlib.pyplot as plt
import motiflets.motiflets as mtfls
import motiflets.plotting as mtfls_plt
from tests.audio.lyrics import *
import motiflets_uni.motiflets as mtfls_uni
from motiflets_uni.plotting import Motiflets as Motiflets_uni
from sklearn.decomposition import PCA
import seaborn as sns

/home/niyaz/Programme/miniconda3/envs/ubuntu-motiflets-mv/lib/python3.8/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
k_max = 25
motif_length = 180
n_dims_rest = 3
n_dims_rest2 = 2

mpl.rcParams['figure.dpi'] = 300

path = "datasets/audio/"
ground_truth_path = "datasets/ground_truth/"


dataset = "Vanilla_Ice-Ice_Ice_Baby"
ds_name = "Vanilla Ice - Ice Ice Baby"

audio_file_url = path + dataset + ".mp3"
audio_length_seconds, df, index_range = read_mp3(audio_file_url)
channels = ['MFCC 0', 'MFCC 1', 'MFCC 2', 'MFCC 3']
df = df.loc[channels]

new_len = int(df.shape[1] - ((df.shape[1]/audio_length_seconds) * 35))
audio_length_seconds_new = audio_length_seconds - 35

df = df.iloc[:,:new_len]
print((df.shape[1]/audio_length_seconds) * 4)


/home/niyaz/Programme/miniconda3/envs/ubuntu-motiflets-mv/lib/python3.8/site-packages/librosa/core/audio.py:171: FutureWarning: librosa.core.audio.__audioread_load
	Deprecated as of librosa version 0.10.0.
	It will be removed in librosa version 1.0.
  y, sr_native = __audioread_load(path, offset, duration, dtype)


Length: 22050 in seconds 271.4916780045352 s
150.05984824079746


/home/niyaz/Bibliothek/GitHub/Bachlorarbeit/Code/motiflets-mv_tests/tests/audio/lyrics.py:14: FutureWarning: get_duration() keyword argument 'filename' has been renamed to 'path' in version 0.10.0.
	This alias will be removed in version 1.0.
  audio_length_seconds = librosa.get_duration(filename=audio_file_url)


In [3]:
def norm_extent(df_full, dists, dims, elbows):
    dists_norm = []
    for elbow in range(len(dists)):
        if dims[elbow] is None:
            dists_norm.append(None)
            continue
        variance = 1
        for i, column in enumerate(df_full.T):
            if i in dims[elbow]:
                variance = variance + np.var(df_full.T[column].to_numpy())

        dists_norm.append(dists[elbow] / np.sqrt(variance / len(dims)))

    return dists_norm

In [4]:
ml_full = Motiflets(ds_name, df,
                dimension_labels=df.index,
                )

dists_full, motiflets_full, motiflets_dims_full, elbow_points_full = ml_full.fit_k_elbow(
                k_max,
                plot_elbows=False,
                plot_motifs_as_grid=False,
                motif_length=motif_length)

dists_full_norm = norm_extent(df, dists_full, motiflets_dims_full, elbow_points_full)

Data (4, 10185)


Chosen window-size: 180 in 4.2 s
Elbow Points [ 6 22]


In [5]:
ml_rest = Motiflets(ds_name, df,
                dimension_labels=df.index,
                n_dims=n_dims_rest
                )

dists_rest, motiflets_rest, motiflets_dims_rest, elbow_points_rest = ml_rest.fit_k_elbow(
                k_max,
                plot_elbows=False,
                plot_motifs_as_grid=False,
                motif_length=motif_length)

dists_rest_norm = norm_extent(df, dists_rest, motiflets_dims_rest, elbow_points_rest)

Data (4, 10185)


Chosen window-size: 180 in 4.5 s
Elbow Points [ 6 20]


In [6]:
ml_rest2 = Motiflets(ds_name, df,
                dimension_labels=df.index,
                n_dims=n_dims_rest2
                )

dists_rest2, motiflets_rest2, motiflets_dims_rest2, elbow_points_rest2 = ml_rest2.fit_k_elbow(
                k_max,
                plot_elbows=False,
                plot_motifs_as_grid=False,
                motif_length=motif_length)

dists_rest2_norm = norm_extent(df, dists_rest2, motiflets_dims_rest2, elbow_points_rest2)

Data (4, 10185)


Chosen window-size: 180 in 4.6 s
Elbow Points [22]


In [7]:
pca = PCA(n_components=1)
np_pca = pca.fit_transform(df.T)
series_pca = pd.Series(np_pca.flatten(), index=df.T.index, name='Ice Ice Baby PCA')
series_pca.index.name = 'Seconds'

ml_uni = Motiflets_uni(ds_name, series_pca)

dists_uni, motiflets_uni, elbow_points_uni =  ml_uni.fit_k_elbow(
                k_max,
                plot_elbows=False,
                plot_motifs_as_grid=False,
                motif_length=motif_length)

Data 10185


Chosen window-size: 180 in 0.9 s
Elbow Points [ 3 21]


In [8]:
np_data = df.T.to_numpy()
mean_centered_data = np_data - np.mean(np_data, axis=0)

cov_matrix = np.cov(mean_centered_data, rowvar=False)
eigenvalues, eigenvectors = np.linalg.eig(cov_matrix)

first_eigenvalue = eigenvalues[0]

dists_uni_norm = []
for u_dist in dists_uni:
     dists_uni_norm.append(u_dist / np.sqrt(first_eigenvalue))

print(dists_uni_norm)

[0.008510302663441369, 0.008510302663441369, 0.008510302663441369, 0.018827182316820068, 0.051863371800500525, 0.06283911506823263, 0.0815270991019965, 0.10016214436078481, 0.11418111931126884, 0.2033313653040609, 0.21804693157837401, 0.2549909287855794, 0.2630156909347526, 0.4957379226503981, 0.6451779637333485, 0.7593631114936057, 0.78492451043809, 0.824774331594214, 0.8980198663945514, 0.8992553797699562, 0.9786335536882116, 1.00685259108881, 1.067013062872376, 1.08599078323498, 1.08599078323498]


In [9]:
_ , df_gt = mtfls.read_dataset_with_index("vanilla_ice.csv", "vanilla_ice_niyaz3.csv", sampling_factor=20000)
print(df_gt.shape)
my_gt = df_gt["riff (4x)"][0]
print(my_gt)
gt_motiflets = np.array([m[0] for m in my_gt])
print(gt_motiflets)

/home/niyaz/Bibliothek/GitHub/Bachlorarbeit/Code/motiflets-mv_tests/motiflets/motiflets.py:100: FutureWarning: The squeeze argument has been deprecated and will be removed in a future version. Append .squeeze("columns") to the call to squeeze.


  data = pd.read_csv(full_path, index_col=0, squeeze=True)


Dataset Original Length n:  23095
Dataset Sampled Length n:  23095
(1, 1)
[[388, 553], [553, 740], [740, 912], [912, 1087], [2523, 2695], [2695, 2885], [2885, 3059], [3059, 3225], [6102, 6271], [6271, 6459], [6459, 6634], [6634, 6787], [8250, 8415], [8415, 8597], [8597, 8779], [8779, 8929], [9153, 9309], [9309, 9493], [9493, 9706], [9706, 9823]]
[ 388  553  740  912 2523 2695 2885 3059 6102 6271 6459 6634 8250 8415
 8597 8779 9153 9309 9493 9706]


In [10]:
#Ground Truth extent
_, raw_data_for_gt = mtfls.pd_series_to_numpy(df)
D_full_gt, knns_gt = mtfls.compute_distance_matrix(
    raw_data_for_gt, motif_length, k_max,
    slack=0.5,
    sum_dims=False)

gt_dims = [x for x in range(df.shape[0])]
gt_motiflets_np = np.array(gt_motiflets)
#gt_extent = mtfls.get_pairwise_extent(D_full_gt, gt_motiflets_np, gt_dims)

upperbound_gt=np.inf
gt_extent = np.float64(0.0)
for ii in range(len(gt_motiflets_np) - 1):
    i = gt_motiflets_np[ii]

    for jj in range(ii + 1, len(gt_motiflets_np)):
        j = gt_motiflets_np[jj]
        gt_extent = max(gt_extent, D_full_gt[gt_dims, i, j].mean())
        if gt_extent > upperbound_gt:
            gt_extent =  np.inf

print(gt_extent)

468.85452


In [12]:
df_cmp = pd.DataFrame()
dists_cmp = []
dims_cmp = []
minature_labels = []

df_cmp[f'Ground Truth'] = [gt_motiflets.tolist()]
dists_cmp.append(0)
dims_cmp.append([0])
minature_labels.append(f'k={len(gt_motiflets)}, d={round(gt_extent)}')


for elbow in elbow_points_full:
    df_cmp[f'Unrestricted: m={df.shape[0]}, k={elbow}'] = [motiflets_full[elbow].tolist()]
    dists_cmp.append(dists_full_norm[elbow])
    dims_cmp.append(motiflets_dims_full[elbow])
    minature_labels.append(f'k={elbow}, d={round(dists_full[elbow])}')

for elbow in elbow_points_rest:
    df_cmp[f'Restricted: m={n_dims_rest}, k={elbow}'] = [motiflets_rest[elbow].tolist()]
    dists_cmp.append(dists_rest_norm[elbow])
    dims_cmp.append(motiflets_dims_rest[elbow])
    minature_labels.append(f'k={elbow}, d={round(dists_rest[elbow])}')

for elbow in elbow_points_rest2:
    df_cmp[f'Restricted: m={n_dims_rest2}, k={elbow}'] = [motiflets_rest2[elbow].tolist()]
    dists_cmp.append(dists_rest2_norm[elbow])
    dims_cmp.append(motiflets_dims_rest2[elbow])
    minature_labels.append(f'k={elbow}, d={round(dists_rest2[elbow])}')

for elbow in elbow_points_uni:
    df_cmp[f'PCA, k={elbow}'] = [motiflets_uni[elbow].tolist()]
    dists_cmp.append(dists_uni[elbow])
    dims_cmp.append(motiflets_dims_full[elbow]) # Use all dimensions
    minature_labels.append(f'k={elbow}, d={round(dists_uni[elbow])}')

#df_cmp[f'Unrestricted'] = [motiflets_uni[20].tolist()]

df_cmp = df_cmp.T
df_cmp.columns = ["offsets"]
print(df_cmp.shape)

elbow_points = [x for x in range(0, df_cmp.shape[0])]

#mtfls_plt.plot_competitors(df, ds_name, df_cmp.offsets.values, motif_length=180)

print(df_cmp.index)

color_indicator = [0, 1, 2, 2, 3, 3, 4, 5, 5]
colors = sns.color_palette("tab10")
my_color_palette = [colors[i] for i in color_indicator]

mtfls_plt.plot_grid_motiflets_niyaz(
    ds_name, df, df_cmp.offsets.values, elbow_points,
    dists_cmp, motif_length,
    dimension_labels=df.index,
    method_names=df_cmp.index,
    ground_truth=gt_motiflets,
    ts_label=f'riff (4x)',
    x_label="Seconds",
    minature_labels=minature_labels,
    font_size=40,
    #color_indicator=color_indicator,
    color_palette=my_color_palette,
    save_path="../../Latex/BachelorarbeitFinal/Images/qual/vanilla.pdf"
    )

    #ground_truth=ground_truth)

(8, 1)
Index(['Ground Truth', 'Unrestricted: m=4, k=6', 'Unrestricted: m=4, k=22',
       'Restricted: m=3, k=6', 'Restricted: m=3, k=20',
       'Restricted: m=2, k=22', 'PCA, k=3', 'PCA, k=21'],
      dtype='object')


/home/niyaz/Bibliothek/GitHub/Bachlorarbeit/Code/motiflets-mv_tests/motiflets/plotting.py:1889: UserWarning: The figure layout has changed to tight
  plt.tight_layout()
/home/niyaz/Bibliothek/GitHub/Bachlorarbeit/Code/motiflets-mv_tests/motiflets/plotting.py:1890: UserWarning: This figure includes Axes that are not compatible with tight_layout, so results might be incorrect.
  gs.tight_layout(fig)
